# Routines to plot out band structures for 2D arrays of linear and horn shaped dispersions

Requires Julia v0.6, the Plots package, and the PyPlot and PlotlyJS backends for Plots, to be installed (use Pkg.add("Plots"), Pkg.add("PyPlot"), Pkg.add("PlotlyJS") if they are missing)

### Inputs

In [12]:
# Input second real space lattice vector (b) as a magnitude and argument
# relative to first real space lattice vector (a) which is assumed to be a_x=0, a_y=1
# arg_b must be between pi/4 and 3*pi/4

mag_b=1
arg_b=pi/3

# Input No. of scattering events in direction of lattice vectors that should be taken into account
# Scattering events in the range between +Nmax and -Nmax along vectors a and b will be included. 

Nmax=3

# Functions for dispersion - just leave one uncommented that you want to use.
# Also we need the inverse function for later plots

function dispersion(z,r)
    # Horn Shape
    #z=r./(1+r)
    # Linear
    z=r/5
end

function dispersion_inverse(z,r)
    # Horn Shape
    #r=z/(1-z)
    # Linear
    r=z*5
end

dispersion_inverse (generic function with 1 method)

In [13]:
#Get things ready

using Plots
plotlyjs(size=(500,500))

# Real space vectors
ax=0.0
ay=1.0
by=mag_b*cos(arg_b)
bx=mag_b*sin(arg_b)
a=[ax,ay]
b=[bx,by]

# Reciprocal lattice vectors
A=2.0*pi*[by/(ax*by - ay*bx),-bx/(ax*by - ay*bx)]
B=2.0*pi*[ay/(bx*ay - by*ax),-ax/(bx*ay - by*ax)]

# Create array of points in reciprocal and real space

Klx=[]
Kly=[]
Xlx=[]
Xly=[]
for n=-Nmax:Nmax
    for m=-Nmax:Nmax
        tempK=n*A+m*B
        tempX=n*a+m*b
        append!(Klx,tempK[1])
        append!(Kly,tempK[2])
        append!(Xlx,tempX[1])
        append!(Xly,tempX[2])
    end
end

### Plot real space lattice points and vectors

In [14]:
# Plot lattice points
scatter(Xlx,Xly)

# Plot lattice vectors
plot!([0,a[1]],[0,a[2]])
plot!([0,b[1]],[0,b[2]],color="green",legend=:none)

# Additional plot attributes
xlims!(-2,2)
ylims!(-2,2)
title!("Real space lattice")
xlabel!("kx")
ylabel!("ky")

### Plot reciprocal space lattice points and vectors, and the BZ


In [6]:
# Plot lattice points
scatter(Klx,Kly)

# Plot lattice vectors
plot!([0,A[1]],[0,A[2]])
plot!([0,B[1]],[0,B[2]],color="green",legend=:none)

# Plot BZ
p1=[0,0]
p2=[B[1]/2,0]
if(arg_b>=pi/2)
    p3=[B[1]/2,B[1]/2*tan(acos(dot(A,B+A)/(norm(A)*norm(B+A)))/2)]
else
    p3=[B[1]/2,B[1]/2*tan(acos(dot(A,B+A)/(norm(A)*norm(B+A)))/2)]
end
plot!([p1[1],p2[1],p3[1],p1[1]],[p1[2],p2[2],p3[2],p1[2]],fill=(0,:grey))

# Additional plot attributes
xlims!(-15,15)
ylims!(-15,15)
title!("Reciprocal space lattice")
xlabel!("kx")
ylabel!("ky")

### Create a 3D plot of the band structure

In [17]:
# Plot limits
xmin=-10
xmax=10
ymin=-10
ymax=10
zmin=0
zmax=1

# Generate x and y co-ordinates in grid and initialise z matrix
x_p=linspace(-10,10,50)
y_p=linspace(-10,10,50)
x=repmat(x_p',50,1)
y=repmat(y_p,1,50)
z=ones(50,50)

# Plot unscattered dispersion
r=sqrt.(x.^2+y.^2)
z=dispersion(z,r)
surface(x,y,z,color="blue",legend=:none,aspect_ratio=10)

# Plot scattered dispersions
for i=1:size(Klx,1)
    r=sqrt.((x+Klx[i]).^2+(y+Kly[i]).^2)
    z=dispersion(z,r)
    surface!(x,y,z,color="blue",legend=:none,clims=(zmin,zmax),zlims=(zmin,zmax),zlabel="f")
end

# Additional Plot attributes
xlims!(xmin,xmax)
ylims!(ymin,ymax)
xlabel!("kx")
ylabel!("ky")

### Plot an iso-frequency contour at specific z value

In [9]:
# z-value to plot at
z=0.8

# Determine radius of isofrequency circles given by the dispersion relation at frequency z
r=0
r=dispersion_inverse(z,r)
    
# Create circle shape for plotting with radius from above
pts=Plots.partialcircle(0,2π,100,r)
x_t, y_t = Plots.unzip(pts)

# Plot unscattered iso-frequency circle
plot(Shape(x_t,y_t),fillalpha=0,legend=:none)

# Plot scattered iso-frequency circles
for i=1:size(Klx,1)
    x=x_t+Klx[i]
    y=y_t+Kly[i]
    plot!(Shape(x,y),fillalpha=0)
end

# Additional plot attributes
xlims!(-15,15)
ylims!(-15,15)
xlabel!("kx")
ylabel!("ky")

### Plot an animation of isofrequency contours as a function of the frequency

In [10]:
# Inputs

zmin=0.5
zmax=1
No_of_frames=30
Frame_rate=5

# Need to use PyPlot backend rather than PlotlyJS for animation - loading up is slow
pyplot()
PyPlot.svg(true)

# This loop generates frames for animation
anim = @animate for i=1:No_of_frames

    # Loop over frequencies
    z=zmin+i*(zmax-zmin)/No_of_frames
    
    # Determine radius of isofrequency circles given by the dispersion relation at frequency z
    r=0
    r=dispersion_inverse(z,r)
    
    # Create circle shape for plotting with radius from above
    pts=Plots.partialcircle(0,2π,100,r)
    x_t, y_t = Plots.unzip(pts)

    # Plot unscattered iso-frequency circle
    plot(Shape(x_t,y_t),fillalpha=0,legend=:none)

    # Plot scattered iso-frequency circles
    for i=1:size(Klx,1)
        x=x_t+Klx[i]
        y=y_t+Kly[i]
        plot!(Shape(x,y),fillalpha=0)
    end

    # Additional plot attributes
    xlims!(-15,15)
    ylims!(-15,15)
    xlabel!("kx")
    ylabel!("ky")
end

# Generate animation and display it
gif(anim, fps = Frame_rate)

INFO: Recompiling stale cache file /Users/ian-work/.julia/lib/v0.6/Conda.ji for module Conda.
INFO: Recompiling stale cache file /Users/ian-work/.julia/lib/v0.6/PyCall.ji for module PyCall.
INFO: Recompiling stale cache file /Users/ian-work/.julia/lib/v0.6/PyPlot.ji for module PyPlot.
INFO: Saved animation to /Users/ian-work/ownCloud/Research/Julia/Misc/tmp.gif


Plots.AnimatedGif("/Users/ian-work/ownCloud/Research/Julia/Misc/tmp.gif")

### Plot the band structure around the BZ

In [35]:
# Inputs - No_of_points is the number of points per section of BZ boundary per band
No_of_points=200
ymin=0
ymax=2


# Go back to PlotlyJS backend - this is slow
plotlyjs(size=(800,500))

# Create kx and ky values around the BZ boundary
points=linspace(0,1,No_of_points)
kx=vcat(points*p2[1],ones(No_of_points)*p2[1],p2[1]-points*p2[1])
ky=vcat(ones(No_of_points)*p2[2],points*p3[2],p3[2]-points*p3[2])

# Create scaled x-axis values for plotting
xaxis=vcat(points*kx[No_of_points],kx[No_of_points]+points*ky[2*No_of_points],kx[No_of_points]+ky[2*No_of_points]+points*(sqrt(kx[No_of_points]^2+ky[2*No_of_points]^2)))

# Create and plot unscattered dispersion
r=sqrt.(kx.^2+ky.^2)
z=dispersion(z,r)
scatter(xaxis,z,legend=:none,c=:black,m=:1,xticks=[])

# Create and plot scattered dispersions
for i=1:size(Klx,1)
    kx=vcat(points*p2[1],ones(No_of_points)*p2[1],p2[1]-points*p2[1])+Klx[i]
    ky=vcat(ones(No_of_points)*p2[2],points*p3[2],p3[2]-points*p3[2])+Kly[i]
    r=sqrt.(kx.^2+ky.^2)
    z=dispersion(z,r)
    scatter!(xaxis,z,legend=:none,c=:black,m=:1)
end

# Plot vertical lines at symmetry points
plot!([xaxis[No_of_points],xaxis[No_of_points]],[ymin,ymax],ls=:dash,c=:black)
plot!([xaxis[No_of_points*2],xaxis[No_of_points*2]],[ymin,ymax],ls=:dash,c=:black)

# Additional plot attributes
xlims!(0,maximum(xaxis))
ylims!(ymin,ymax)
xlabel!("Wavevector")
ylabel!("Frequency")
